<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Reading-data-scrapped-in-previous-notebook" data-toc-modified-id="Reading-data-scrapped-in-previous-notebook-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Reading data scrapped in previous notebook</a></span><ul class="toc-item"><li><span><a href="#Removing-odd-cases-of-properties-outside-of-Warsaw" data-toc-modified-id="Removing-odd-cases-of-properties-outside-of-Warsaw-1.1"><span class="toc-item-num">1.1&nbsp;&nbsp;</span>Removing odd cases of properties outside of Warsaw</a></span></li></ul></li><li><span><a href="#Basic-data-visualization" data-toc-modified-id="Basic-data-visualization-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Basic data visualization</a></span><ul class="toc-item"><li><span><a href="#Visualizing-unit-price-(PLN/m2)-for-each-offer-as-scatter-plot" data-toc-modified-id="Visualizing-unit-price-(PLN/m2)-for-each-offer-as-scatter-plot-2.1"><span class="toc-item-num">2.1&nbsp;&nbsp;</span>Visualizing unit price (PLN/m2) for each offer as scatter plot</a></span></li><li><span><a href="#Grouping-offers-to-create-a-grid" data-toc-modified-id="Grouping-offers-to-create-a-grid-2.2"><span class="toc-item-num">2.2&nbsp;&nbsp;</span>Grouping offers to create a grid</a></span></li><li><span><a href="#Experimenting-with-other-viz-Types" data-toc-modified-id="Experimenting-with-other-viz-Types-2.3"><span class="toc-item-num">2.3&nbsp;&nbsp;</span>Experimenting with other viz Types</a></span><ul class="toc-item"><li><span><a href="#Heatmap" data-toc-modified-id="Heatmap-2.3.1"><span class="toc-item-num">2.3.1&nbsp;&nbsp;</span>Heatmap</a></span></li><li><span><a href="#Surface-plot" data-toc-modified-id="Surface-plot-2.3.2"><span class="toc-item-num">2.3.2&nbsp;&nbsp;</span>Surface plot</a></span></li><li><span><a href="#Contour-plot" data-toc-modified-id="Contour-plot-2.3.3"><span class="toc-item-num">2.3.3&nbsp;&nbsp;</span>Contour plot</a></span></li></ul></li></ul></li><li><span><a href="#Advanced-visualizaiton" data-toc-modified-id="Advanced-visualizaiton-3"><span class="toc-item-num">3&nbsp;&nbsp;</span>Advanced visualizaiton</a></span><ul class="toc-item"><li><span><a href="#Creating-GeoJson-data" data-toc-modified-id="Creating-GeoJson-data-3.1"><span class="toc-item-num">3.1&nbsp;&nbsp;</span>Creating GeoJson data</a></span></li><li><span><a href="#Initial-approach-to-grid-based-choropleth-map" data-toc-modified-id="Initial-approach-to-grid-based-choropleth-map-3.2"><span class="toc-item-num">3.2&nbsp;&nbsp;</span>Initial approach to grid based choropleth map</a></span></li></ul></li></ul></div>

In [52]:
import os
from urllib.request import urlretrieve
from urllib.request import urlopen
from bs4 import BeautifulSoup
import pandas as pd
import numpy as np
import re
import json
import numpy as np
import timeit 
from datetime import datetime

In [220]:
import plotly.express as px

In [54]:
# Cufflinks wrapper on plotly
import cufflinks
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = 'all'

from plotly.offline import iplot
cufflinks.go_offline()

# Set global theme

import plotly.figure_factory as ff

import plotly.graph_objects as go

# Reading data scrapped in previous notebook

In [55]:
df=pd.read_excel("Warsaw_RE_data.xlsx")

In [56]:
df.columns

Index(['Unnamed: 0', 'Id', 'Area', 'Price', 'latitude', 'longitude',
       'build_year', 'building_floors_num', 'rooms_num', 'floors_num', 'City',
       'district', 'market', 'Building_material', 'Building_ownership',
       'Building_type', 'Construction_status', 'floor_no', 'Heating',
       'Windows_type', 'Equipment_types_dishwasher', 'Equipment_types_fridge',
       'Equipment_types_furniture', 'Equipment_types_oven',
       'Equipment_types_stove', 'Equipment_types_tv',
       'Equipment_types_washing_machine', 'Extras_types_air_conditioning',
       'Extras_types_attic', 'Extras_types_balcony', 'Extras_types_basement',
       'Extras_types_garage', 'Extras_types_garden', 'Extras_types_lift',
       'Extras_types_separate_kitchen', 'Extras_types_terrace',
       'Extras_types_two_storey', 'Extras_types_usable_room',
       'Media_types_cable-television', 'Media_types_electricity',
       'Media_types_internet', 'Media_types_phone', 'Media_types_sewage',
       'Media_types_wate

In [57]:
df.shape

(11939, 50)

## Removing odd cases of properties outside of Warsaw

In [58]:
df=df.query("City=='warszawa'")
df=df.query("latitude>52 and latitude<53")
df=df.query("longitude>20 and longitude<21.2")

In [59]:
df.shape

(11884, 50)

In [60]:
df.groupby("district", as_index=False).count()[["district","Id"]].sort_values(by="Id",ascending=False).head(10)

district    Id
115            Wola  1312
44          Mokotów  1185
126     Śródmieście   903
4         Białołęka   851
70   Praga-Południe   662
3            Bemowo   587
106           Ursus   498
107         Ursynów   425
112         Wilanów   425
120          Włochy   410

In [61]:
df["unit_price"]=df.Price/df.Area

# Basic data visualization

In [200]:
data=[]
trace0=dict(
            lat=df.latitude,
            lon=df.longitude,
          
            type="scattermapbox",
            mode='markers',
            marker=dict(
                opacity=0.5, 
                size=10, 
                color=df.unit_price,
               
                colorscale="jet",
                cauto=False,
                cmax=20000,
                showscale=True),
                text=df.unit_price,
            
           
            )



data=[trace0]

layout = dict(
    
   
    
    title="Sample size by Production year and condition",
    height = 800,
    # top, bottom, left and right margins
    margin = dict(t = 0, b = 0, l = 0, r = 0),
    font = dict(color = '#FFFFFF', size = 11),
    paper_bgcolor = '#000000',
    mapbox = dict(
        
        # here you need the token from Mapbox
        accesstoken ="pk.eyJ1IjoiamFubWFqZXdza2kiLCJhIjoiY2p1bnRkN2JiMTFuczRjbXFuaDg0YWswZSJ9.LICCkkSfzPTXlNZ3MC-HHg",
        bearing = 0,
        # where we want the map to be centered
        center = dict(
            lat = 52.2,
            lon = 21
        ),
        # we want the map to be "parallel" to our screen, with no angle
        pitch = 0,
        # default level of zoom
        zoom = 10,
        # default map style
        style = 'light'
    )

)

figure=dict(
    data=data,
    layout=layout,
  
    )


## Visualizing unit price (PLN/m2) for each offer as scatter plot

In [201]:
iplot(figure)

## Grouping offers to create a grid

In [13]:
rounding_num=0.008 #roundign coordinates by chosen precision creates a grid
df["lon_mod"]=np.round(df.longitude/rounding_num,0)*rounding_num


df["lat_mod"]=np.round(df.latitude/rounding_num,0)*rounding_num


In [14]:
data=[]
trace0=dict(
            lat=df.lat_mod,
            lon=df.lon_mod,
          
            type="scattermapbox",
            mode='markers',
            marker=dict(
                opacity=0.5, 
                size=10, 
                color=df.unit_price,
               
                colorscale="jet",
                cauto=False,
                cmax=20000,
                showscale=True),
                text=df.unit_price,
            
           
            )



data=[trace0]

layout = dict(
    
   
    height = 800,
    # top, bottom, left and right margins
    margin = dict(t = 0, b = 0, l = 0, r = 0),
    font = dict(color = '#FFFFFF', size = 11),
    paper_bgcolor = '#000000',
    mapbox = dict(
        # here you need the token from Mapbox
        accesstoken ="pk.eyJ1IjoiamFubWFqZXdza2kiLCJhIjoiY2p1bnRkN2JiMTFuczRjbXFuaDg0YWswZSJ9.LICCkkSfzPTXlNZ3MC-HHg",
        bearing = 0,
        # where we want the map to be centered
        center = dict(
            lat = 52.2,
            lon = 21
        ),
        # we want the map to be "parallel" to our screen, with no angle
        pitch = 0,
        # default level of zoom
        zoom = 10,
        # default map style
        style = 'light'
    )
)

figure=dict(
    data=data,
    layout=layout
    )
iplot(figure)

## Experimenting with other viz Types

In [202]:
df_piv=df.pivot_table(index="lat_mod",columns="lon_mod",values="unit_price",aggfunc=np.mean)

In [203]:
arr=df_piv.values

In [204]:
df_piv.columns.shape

(37,)

In [205]:
df_piv.index.shape

(29,)

### Heatmap

In [206]:
fig = go.Figure(data=go.Heatmap(
                   z=df_piv.values,
                   y=df_piv.index,
                   x=df_piv.columns,
                 ))
fig.show()

### Surface plot

In [208]:
trace0=go.Surface(
        z=df_piv.values,
        y=df_piv.index,
        x=df_piv.columns,
       connectgaps=True
          

        )

data=[trace0]

In [209]:
figure=go.Figure(
    data=data,
    layout=go.Layout(
      
        scene=dict(
            xaxis=dict(title="Longitude"),
            yaxis=dict(title="Latitude"),
            zaxis=dict(title="Price per m2")

           
                  ),
         title="Real estate price per m2 geo distribution"
    ))
iplot(figure)

### Contour plot

In [211]:
fig = go.Figure(data =
    go.Contour(
        z=df_piv.values,
        y=df_piv.index,
        x=df_piv.columns,
        connectgaps=True
    ))
fig.show()

# Advanced visualizaiton

Scatter plots work well with maps, but they tend to be too crowded, on the other hand, the other surface plots are easier to read, but cannot be combined with a map using plotly. A choropleth map with custom created geojson object will probably be the best solution. 

In [212]:
df_map=df[["lat_mod","lon_mod","unit_price"]].groupby(["lat_mod","lon_mod"], as_index=False).mean()


In [221]:
df_map["sample"]=df[["lat_mod","lon_mod","Id"]].groupby(["lat_mod","lon_mod"], as_index=False).count().Id
df_map["district"]=df[["lat_mod","lon_mod","district"]].groupby(["lat_mod","lon_mod"], as_index=False).first().district

In [222]:
df_map["district"]=np.where(df_map.district.isna(),"Other",df_map.district)

In [223]:
df_map.head()

lat_mod  lon_mod    unit_price district  geo_Id  sample
0    52.08    20.96  11484.504490  Jelonki       0       2
1    52.08    21.02   5842.905518  Ursynów       1       1
2    52.10    20.98   4466.019417     Pyry       2       1
3    52.10    20.99   6307.248960  Ursynów       3       3
4    52.10    21.03   6912.291667  Ursynów       4       3

In [216]:
df_map["geo_Id"]=df_map.index

## Creating GeoJson data

In [237]:
geo_list=[]

for i in range(0,df_map.shape[0]):
    point=df_map.iloc[i,:]
    geo_json={}
    geo_json["type"]="Feature"
    
    geo_json["properties"]={"District":point.district}
    
    geo_json["geometry"]={
        "type":"Polygon",
        "coordinates":[[[point.lon_mod+rounding_num/2,point.lat_mod+rounding_num/2],
                        [point.lon_mod-rounding_num/2,point.lat_mod+rounding_num/2],
                        [point.lon_mod-rounding_num/2,point.lat_mod-rounding_num/2],
                        [point.lon_mod+rounding_num/2,point.lat_mod-rounding_num/2]]]}
        
    geo_json["id"]=i
    
    geo_list.append(geo_json)


In [238]:
len(geo_list)

460

In [239]:
sub_districts={"type":"FeatureCollection","features":geo_list}

## Initial approach to grid based choropleth map

In [243]:
fig = px.choropleth_mapbox(df_map,
                    geojson=sub_districts, 
                    locations='geo_Id',
                    color='unit_price', 
                    color_continuous_scale="jet",


                    mapbox_style='open-street-map',
                    zoom=9, center={"lat": 52.2, "lon": 21},
                    opacity=0.5,
                    hover_name="district",
                    hover_data=["sample"]
                           

                           
                          )

fig.show()